# 1. 모듈설정

In [6]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import time
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.by import By
import requests
from bs4 import BeautifulSoup
import urllib.request
from urllib.request import Request, urlopen   
import urllib.parse
from urllib.parse import quote
import sys
import pandas as pd
import datetime
from datetime import timedelta
from PIL import Image
from io import BytesIO

# 2. 최종 크롤링 코드

In [3]:
idx = 0
k = 0
cur_page = 1
news_num = 20


titles = []
texts = []
urls = []
dates = []
fields = []

img_tits = []
img_urls = []
img_dates = []
img_fields = []


start_date='20210106'
end_date='20211231'
date_list=pd.Series(pd.date_range(start=start_date, end=end_date, freq='B')).dt.strftime("%Y.%m.%d.")



while k < len(date_list)+1:
    while idx < news_num:
        news_url = 'https://www.hankyung.com/all-news/?sdate='+date_list[k]+'&edate='+date_list[k]+'&page='
        news_url_1 = news_url + str(cur_page)
        driver = webdriver.Chrome(ChromeDriverManager().install())
        driver.get(news_url_1)
        time.sleep(2)

        html = driver.page_source
        soup = BeautifulSoup(html, 'lxml') #html.parser 

        ul = soup.find_all('ul', class_ = "article_list")
        
        if ul == []:
            k += 1 
            cur_page = 1
            news_url = 'https://www.hankyung.com/all-news/?sdate='+date_list[k]+'&edate='+date_list[k]+'&page='
            news_url_1 = news_url + str(cur_page)
            driver = webdriver.Chrome(ChromeDriverManager().install())
            driver.get(news_url_1)
            time.sleep(2)

            html = driver.page_source
            soup = BeautifulSoup(html, 'lxml') #html.parser 

            ul = soup.find_all('ul', class_ = "article_list")
            divs_img = ul[0].find_all('div', class_= "thumb")
            h3_list = ul[0].find_all('h3', class_= "tit")
            divs_txt = ul[0].find_all('p', class_= "read")     

        elif ul !=[]:
            divs_img = ul[0].find_all('div', class_= "thumb")
            h3_list = ul[0].find_all('h3', class_= "tit")
            divs_txt = ul[0].find_all('p', class_= "read") 

        for n in h3_list:
            for i in divs_img:   
                for p in range(len(divs_txt)):
                    text = divs_txt[p].text
                    texts.append(text)
                img_tit = i.find('img')['alt'].replace("&#039;","").replace("&quot;","").replace("''","").replace("""""","").replace("‘","").replace("’","").replace("&amp;","")
                img_tits.append(img_tit)
                img_url_ = i.find('img')['src']
                img_url = 'https:' + img_url_
                img_urls.append(img_url)
                img_link = i.find('a')['href']
                img_date = img_link[-13:-5]
                img_dates.append(img_date)
                img_field = img_link[25:-22]
                img_fields.append(img_field)
            title = n.find('a').text.replace('"','').replace("'","")
            titles.append(title)
            url = n.find('a')['href']
            urls.append(url)
            field = url[25:-22]
            fields.append(field)
            date = url[-13:-5]
            dates.append(date)
            
            idx += 1
            
            if idx == news_num:
                cur_page += 1
                driver.get(news_url + str(cur_page))
                time.sleep(2)
                html = driver.page_source
                soup = BeautifulSoup(html, 'lxml') #html.parser
                idx = 0

                import pandas as pd
                df_text_ = pd.DataFrame({'headline': titles, 'url': urls, 'date': dates, 'field': fields}).drop_duplicates()
                df_contents = pd.DataFrame({'text': texts}).drop_duplicates()
                df_text = pd.concat([df_text_, df_contents], axis=1).drop_duplicates()
                
                df_text_1 = df_text[(df_text['field']=='international')|(df_text['field']=='finance')|(df_text['field']=='economy')|(df_text['field']=='politics')|(df_text['field']=='realestate')|(df_text['field']=='opinion')]
                df_text_1 = df_text_1.drop_duplicates().reset_index()
                df_text_1['img_url'] = 0

                df_img = pd.DataFrame({'headline': img_tits, 'img_url': img_urls, 'date': img_dates, 'field': img_fields}).drop_duplicates()
                df_img_1 = df_img[(df_img['field']=='international')|(df_img['field']=='finance')|(df_img['field']=='economy')|(df_img['field']=='politics')|(df_img['field']=='realestate')|(df_img['field']=='opinion')].drop_duplicates()
                df_img_1 = df_img_1.drop_duplicates().reset_index()
                df_img_1['url'] = 0

                df = pd.merge(df_text_1, df_img_1, on='headline', how='outer')
                df = df[['headline', 'date_x', 'field_x', 'url_x', 'img_url_y', 'text']].rename(columns = {'headline':'headline', 'date_x':'date', 'field_x':'field', 'url_x':'url', 'img_url_y':'img_url', 'text':'text'}).dropna(subset='date').fillna("")
                df = df.drop_duplicates().reset_index()

                print(df)
                print(cur_page)


C:\Users\admin\AppData\Local\Temp\ipykernel_2508\6548914.py:29: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


   index                             headline      date          field  \
0      0   미 12월 민간 일자리, 팬데믹 초기 이후 8개월만에 첫 감소  20210106  international   
1      1         이스라엘과 수교 수단, 세계은행에서 자금 조달 가능  20210106  international   
2      2    트럼프 운명의 날…펜스에 크게 용기낼 때 대선불복 거듭 압박  20210106  international   
3      3        터키·이란, 아랍 4개국과 카타르 외교관계 복원 환영  20210106  international   
4      4     바이든 대선승리 확정 마지막 관문…美의회 논란끝 인증 전망  20210106  international   
5      5  정 총리, 대설·한파 긴급 지시…출근시간 조정 등 적극 시행하라  20210106       politics   
6      6          정총리 대설특보 지역 출근시간 조정 각급기관 지시  20210106       politics   
7      7          미 민주 트리플 크라운 달성하나…상원 장악도 성큼  20210106  international   

                                                 url  \
0  https://www.hankyung.com/international/article...   
1  https://www.hankyung.com/international/article...   
2  https://www.hankyung.com/international/article...   
3  https://www.hankyung.com/international/article...   
4  https://www.hankyung.com/international/article... 

C:\Users\admin\AppData\Local\Temp\ipykernel_2508\6548914.py:29: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


    index                               headline      date          field  \
0       0     미 12월 민간 일자리, 팬데믹 초기 이후 8개월만에 첫 감소  20210106  international   
1       1           이스라엘과 수교 수단, 세계은행에서 자금 조달 가능  20210106  international   
2       2      트럼프 운명의 날…펜스에 크게 용기낼 때 대선불복 거듭 압박  20210106  international   
3       3          터키·이란, 아랍 4개국과 카타르 외교관계 복원 환영  20210106  international   
4       4       바이든 대선승리 확정 마지막 관문…美의회 논란끝 인증 전망  20210106  international   
5       5    정 총리, 대설·한파 긴급 지시…출근시간 조정 등 적극 시행하라  20210106       politics   
6       6            정총리 대설특보 지역 출근시간 조정 각급기관 지시  20210106       politics   
7       7            미 민주 트리플 크라운 달성하나…상원 장악도 성큼  20210106  international   
8       8  유럽의약품청, 모더나 백신 승인 권고…화이자 이어 두번째(종합2보)  20210106  international   
9       9        영국서 미국 송환 위기 면한 어산지, 보석 신청은 불허돼  20210106  international   
10     10                 김영춘 부산을 동북아 싱가포르로 만들 것  20210106       politics   
11     11       프랑스 유명 정치학자, 미성년 의붓아들 성폭행 혐의로 수사  20210106  international   

C:\Users\admin\AppData\Local\Temp\ipykernel_2508\6548914.py:29: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


...

       index                            headline      date          field  \
0          0  미 12월 민간 일자리, 팬데믹 초기 이후 8개월만에 첫 감소  20210106  international   
1          1        이스라엘과 수교 수단, 세계은행에서 자금 조달 가능  20210106  international   
2          2   트럼프 운명의 날…펜스에 크게 용기낼 때 대선불복 거듭 압박  20210106  international   
3          3       터키·이란, 아랍 4개국과 카타르 외교관계 복원 환영  20210106  international   
4          4    바이든 대선승리 확정 마지막 관문…美의회 논란끝 인증 전망  20210106  international   
...      ...                                 ...       ...            ...   
10979  10979                  문대통령, 황희 문체부 장관 임명  20210210       politics   
10980  10980     인도네시아 추락기 엔진 출력조절장치 문제…예비보고서 발표  20210210  international   
10981  10981     AZ백신 고령층 접종 어떻게…영국은 모두·EU는 연령제한  20210210  international   
10982  10982       미국 리조트 개발 좌초에 국내기관 수천억대 손실 위기  20210210        economy   
10983  10983        중국 미국도 우리처럼 투명하게 코로나19 조사받아라  20210210  international   

                                                     url  \
0      https://

C:\Users\admin\AppData\Local\Temp\ipykernel_2508\6548914.py:29: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


       index                                           headline      date  \
0          0                 미 12월 민간 일자리, 팬데믹 초기 이후 8개월만에 첫 감소  20210106   
1          1                       이스라엘과 수교 수단, 세계은행에서 자금 조달 가능  20210106   
2          2                  트럼프 운명의 날…펜스에 크게 용기낼 때 대선불복 거듭 압박  20210106   
3          3                      터키·이란, 아랍 4개국과 카타르 외교관계 복원 환영  20210106   
4          4                   바이든 대선승리 확정 마지막 관문…美의회 논란끝 인증 전망  20210106   
...      ...                                                ...       ...   
10989  10989                      10일, 거래소 외국인 순매수상위에 화학 업종 5종목  20210210   
10990  10990  10일, 기관 거래소에서 LG전자(+4.04%), KODEX 레버리지(+1.32%)...  20210210   
10991  10991   10일, 외국인 거래소에서 삼성전자(-1.33%), 현대모비스(+1.84%) 등 순매도  20210210   
10992  10992                  이인영 새해 더 큰 평화 열고자 노력…북녘 동포들도 건강하길  20210210   
10993  10993                      변창흠 2·4 공급 대책으로 집값 내릴 수도 있을 것  20210210   

               field                                                url  \


C:\Users\admin\AppData\Local\Temp\ipykernel_2508\6548914.py:29: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())
C:\Users\admin\AppData\Local\Temp\ipykernel_2508\6548914.py:43: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


IndexError: list index out of range

In [ ]:
df

# 3. 데이터 저장하기

In [76]:
import pandas as pd 
df = pd.read_csv("C:/Users/admin/RNN/text_n.csv", encoding='cp949')

In [126]:
for m in range(16976, 95362): 
    date_img = str(int(df.iloc[m].loc['date']))
    img_link = df.iloc[m].loc['img_url']
    urllib.request.urlretrieve(img_link,"D:/Dropbox/image/negative/" + date_img + "_n_"+ str(m) +".jpg") # download images in address folder

ValueError: cannot convert float NaN to integer

In [77]:
range(len(df['img_url']))

range(0, 95362)

In [70]:
img_link = df.iloc[m].loc['img_url']
img_link

nan

In [71]:
import math
date_img = str(int(df.iloc[m].loc['date']))
date_img

ValueError: cannot convert float NaN to integer